# Prepare Dispersal unit type data from TRY for use

The dispersal unit type data from TRY informs on different aspects of dispersal. It is not a homogeneous trait, and therefore data is split and allocated to different traits in the pre-processing process, namely "Fruit type", "Fruit carpel development type", and "Dispersal unit type".

*If you intend to clean more than one or two traits, we recommend the use of the batch pre-processing script. Refer to the [TRY main page](try-label) for details.*

If you have questions, suggestions, spot errors, or want to contribute, get in touch with us through planthub@idiv.de.

Author: David Schellenberger Costa

## Requirements

To run the script, the following is needed:
- TRY data, available <a href="https://planthub.idiv.de/downloads/" target="_parent">here</a>
- the data.table library may need to be installed

## Code

In [11]:
# load in libraries
library(data.table) # handle large datasets

# clear workspace
rm(list = ls())


Let's get the TRY data

In [ ]:
# set working directory (adapt this!)
setwd(paste0(.brd, "PlantHub"))

# read in data (adapt this!)
TRY <- fread("TRY_PlantHub.gz")

# select data of interest
TRYSubset <- TRY[TraitName == "Dispersal unit type"]


To get an overview of the data, we convert values to lowercase, sort them, and show them as
a table.

In [ ]:
# extract original data strings
oriVals <- TRYSubset$OrigValueStr # oriVals == original values

# change all to lowercase to ease later classification
oriVals <- tolower(oriVals)

# get an overview over the data by summarizing values and showing them in alphabetical order
valueOverview <- table(oriVals)
valueOverview[order(valueOverview)]


Some entries are just the word "yes". This should be decoded. It also looks like a good idea to remove purely numeric values.

In [ ]:
# decode coded entries
oriVals[TRYSubset$DatasetID == 92 & oriVals == "yes"] <- "small grain"

# remove purely numeric values and others that have no lowercase character included
oriVals[!grepl("[[:lower:]]", oriVals)] <- NA


The most important part of the cleaning process is the definition of the search strings to look for.
We use regular expressions in some cases to be more inclusive (or exclusive).

In [ ]:
searchNames <- c(
	# number of seeds
	"one-seeded",
	"multi-seeded",
	# type 1
	"generative",
	"vegetative",
	# type 2
	"infructescence",
	"germinule",
	"cone|gimn",
	"^seed$|small grain",
	"fr?uit(\\W|$)| seed \\(with testa\\)",
	"fruitlet|fr?uit segment",
	"spore",
	# type 3
	"pappus|achene",
	"pod",
	"utricul",
	"berr",
	"drup",
	"aril",
	# carpel development
	"mericarp",
	"syncarp"
)


We can now search for the strings defined before and give names to the new categories. We also prepare a matrix to store the results.

In [ ]:
# search for the strings defined before
searchResults <- sapply(searchNames, grepl, oriVals)

# name columns of searchResults matrix like corrected searchNames
searchResultsCols <- list()
searchResultsCols[[1]] <- c(
	"one-seeded", "multi-seeded",
	"generative", "vegetative",
	"infructescence", "germinule", "cone", "seed", "fruit", "fruitlet", "spore"
)
searchResultsCols[[2]] <- c("dry,achene", "dry,pod", "dry,utricle", "fleshy,berry", "fleshy,drupe", "aril")
searchResultsCols[[3]] <- c("schizocarp", "syncarp")
colnames(searchResults) <- unlist(searchResultsCols)

# prepare matrix to save new values in
newVals <- matrix(NA, length(oriVals), length(searchResultsCols))


Let's have a look at the results.

In [ ]:
# show the number of matches to each category
colSums(searchResults)

# show the original entries for which no match was retrieved
sort(table(oriVals[rowSums(searchResults) < 1]))

# show the number of entries that weren't matched to any category
sum(rowSums(searchResults) < 1)

# show the number of entries that were matched to more that one category
sum(rowSums(searchResults) > 1)


Some of the categories defined have exclusive values, so we remove ambiguous entries.

In [ ]:
# remove contradictory entries
for (i in c(2, 3)) {
	searchResults[
		rowSums(searchResults[, colnames(searchResults) %in% searchResultsCols[[i]]]) > 1,
		colnames(searchResults) %in% searchResultsCols[[i]]
	] <- FALSE
}
searchResults[
	rowSums(searchResults[, grep("seeded", colnames(searchResults))]) > 1,
	grep("seeded", colnames(searchResults))
] <- FALSE
searchResults[
	rowSums(searchResults[, grep("ative", colnames(searchResults))]) > 1,
	grep("ative", colnames(searchResults))
] <- FALSE
searchResults[
	rowSums(searchResults[, grep("^(infructescence|germinule|cone|seed|fruit|fruitlet|spore)", colnames(searchResults))]) > 1,
	grep("^(infructescence|germinule|cone|seed|fruit|fruitlet|spore)", colnames(searchResults))
] <- FALSE


We can now fill the cleaned values into the new values matrix. Then, we transfer the data to other traits, if necessary. Finally, we integrate the data into the TRY dataset.

In [ ]:
# use the searchResults matrix to create new value strings by concatenating all data found
for (i in seq_along(searchResultsCols)) {
	searchResultsTemp <- searchResults[, colnames(searchResults) %in% searchResultsCols[[i]], drop = FALSE]
	newVals[, i] <- sapply(seq_len(nrow(searchResultsTemp)), function(x) {
		paste(searchResultsCols[[i]][searchResultsTemp[x, ]], collapse = ",")
	})
}
newVals[newVals == ""] <- NA

# move values to other traits
traitNames <- c("gotoFruit type", "gotoFruit carpel development type")
for (i in seq_along(traitNames)) {
	if (i > 1) TRY <- rbind(TRY, TRYSubset, fill = TRUE)
	TRY[TraitName == "Dispersal unit type", CleanedValueStr := newVals[, i + 1]]
	TRY[TraitName == "Dispersal unit type", TraitName := traitNames[i]]
}

# integrate into TRY
TRY[TraitName == "Dispersal unit type", CleanedValueStr := newVals[, 1]]


As we duplicated the data to accommodate the data belonging to other traits, to avoid an unnecessary increase
in file size, we remove the rows of the duplicated data without values in the "CleanedValueStr" column.

In [ ]:
# remove duplicated rows without new data
TRY <- TRY[!grepl("^goto", TraitName) | !is.na(CleanedValueStr)]


We have used an existing trait name with the prefix "goto" to classify some data. This was done
to eventually move the data to the respective trait, but avoid another round of pre-processing.
So only run the following line if this is the last of various pre-processing scripts you want to use.

In [ ]:
# remove "goto" before trait name (do this after the last script only when executing various scripts
# to avoid duplications and other errors)
TRY[, TraitName := sub("^goto", "", TraitName)]


Let's write the data to a file.

In [ ]:
# write data
fwrite(TRY, file = paste0("TRY_processed_", Sys.Date(), ".gz"))
